**Setting Up Environment**

In [1]:
! pip install pycaret[full]

     |████████████████████████████████| 266kB 5.3MB/s 
     |████████████████████████████████| 276kB 29.7MB/s 
     |████████████████████████████████| 6.8MB 28.7MB/s 
     |████████████████████████████████| 61kB 6.5MB/s 
     |████████████████████████████████| 14.2MB 339kB/s 
     |████████████████████████████████| 245kB 35.1MB/s 
     |████████████████████████████████| 1.7MB 37.3MB/s 
     |████████████████████████████████| 1.8MB 37.7MB/s 
     |████████████████████████████████| 215kB 39.2MB/s 
     |████████████████████████████████| 102kB 9.1MB/s 
     |████████████████████████████████| 358kB 40.0MB/s 
     |████████████████████████████████| 157.5MB 67kB/s 
     |████████████████████████████████| 102kB 9.2MB/s 
     |████████████████████████████████| 65.7MB 60kB/s 
     |████████████████████████████████| 348kB 40.1MB/s 
     |████████████████████████████████| 296kB 40.4MB/s 
     |████████████████████████████████| 47.5MB 76kB/s 
     |████████████████████████████████| 3.6MB 39.3MB/s 

In [2]:
from pycaret.utils import enable_colab
enable_colab()

Colab mode enabled.


**Importing Dataset**

In [9]:
from pycaret.datasets import get_data
dataset = get_data('traffic')

holiday    temp  rain_1h  ...  weather_main  Rush Hour traffic_volume
0    None  288.28      0.0  ...        Clouds          1           5545
1    None  289.36      0.0  ...        Clouds          0           4516
2    None  289.58      0.0  ...        Clouds          0           4767
3    None  290.13      0.0  ...        Clouds          0           5026
4    None  291.14      0.0  ...        Clouds          0           4918

[5 rows x 8 columns]

In [10]:
#check the shape of data
dataset.shape

(48204, 8)

In [11]:
data = dataset.sample(frac=0.7)
data_unseen = dataset.drop(data.index)

data.reset_index(drop=True, inplace=True)
data_unseen.reset_index(drop=True, inplace=True)

print('Data for Modeling: ' + str(data.shape))
print('Unseen Data For Predictions: ' + str(data_unseen.shape))

Data for Modeling: (33743, 8)
Unseen Data For Predictions: (14461, 8)


In [12]:
from pycaret.anomaly import *

exp_ano101 = setup(data)

Description                 Value
0                               session_id                  8240
1                            Original Data            (33743, 8)
2                           Missing Values                 False
3                         Numeric Features                     5
4                     Categorical Features                     3
5                         Ordinal Features                 False
6                High Cardinality Features                 False
7                  High Cardinality Method                  None
8                         Transformed Data           (33743, 30)
9                                 CPU Jobs                    -1
10                                 Use GPU                 False
11                          Log Experiment                 False
12                         Experiment Name  anomaly-default-name
13                                     USI                  0763
14                         Imputation Type                simple
15          Iterative Imputation Iteration                  None
16                         Numeric Imputer                  mean
17      Iterative Imputation Numeric Model                  None
18                     Categorical Imputer                  mode
19  Iterative Imputation Categorical Model                  None
20           Unknown Categoricals Handling        least_frequent
21                               Normalize                 False
22                        Normalize Method                  None
23                          Transformation                 False
24                   Transformation Method                  None
25                                     PCA                 False
26                              PCA Method                  None
27                          PCA Components                  None
28                     Ignore Low Variance                 False
29                     Combine Rare Levels                 False
30                    Rare Level Threshold                  None
31                         Numeric Binning                 False
32                         Remove Outliers                 False
33                      Outliers Threshold                  None
34                Remove Multicollinearity                 False
35             Multicollinearity Threshold                  None
36                              Clustering                 False
37                    Clustering Iteration                  None
38                     Polynomial Features                 False
39                       Polynomial Degree                  None
40                    Trignometry Features                 False
41                    Polynomial Threshold                  None
42                          Group Features                 False
43                       Feature Selection                 False
44                Feature Selection Method               classic
45            Features Selection Threshold                  None
46                     Feature Interaction                 False
47                           Feature Ratio                 False
48                   Interaction Threshold                  None

**Create Model**


In [13]:
iforest = create_model('iforest')
print(iforest)

IForest(behaviour='new', bootstrap=False, contamination=0.05,
    max_features=1.0, max_samples='auto', n_estimators=100, n_jobs=-1,
    random_state=8240, verbose=0)


**Assign Anomaly Labels**

In [14]:
iforest_results = assign_model(iforest)
iforest_results.head()

holiday    temp  rain_1h  ...  traffic_volume  Anomaly Anomaly_Score
0    None  248.61     0.00  ...            5494        1      0.001494
1    None  267.43     0.00  ...            3449        0     -0.081886
2    None  276.50     0.00  ...            4468        0     -0.075454
3    None  296.41     0.00  ...            4717        0     -0.063563
4    None  288.62     3.45  ...            6354        1      0.025396

[5 rows x 10 columns]

**Analyze Model**

In [15]:
plot_model(iforest)

In [16]:
plot_model(iforest, plot = 'umap')

In [17]:
unseen_predictions = predict_model(iforest, data=data_unseen)
unseen_predictions.head()

holiday    temp  rain_1h  ...  traffic_volume  Anomaly Anomaly_Score
0    None  288.28      0.0  ...            5545        0     -0.071680
1    None  284.63      0.0  ...             506        0     -0.139766
2    None  283.47      0.0  ...             321        0     -0.137538
3    None  278.12      0.0  ...            6511        0     -0.030766
4    None  291.97      0.0  ...            5097        0     -0.137659

[5 rows x 10 columns]

In [19]:
data_predictions = predict_model(iforest, data = data)
data_predictions.head()

holiday    temp  rain_1h  ...  traffic_volume  Anomaly Anomaly_Score
0    None  248.61     0.00  ...            5494        1      0.001494
1    None  267.43     0.00  ...            3449        0     -0.081886
2    None  276.50     0.00  ...            4468        0     -0.075454
3    None  296.41     0.00  ...            4717        0     -0.063563
4    None  288.62     3.45  ...            6354        1      0.025396

[5 rows x 10 columns]

In [20]:
save_model(iforest,'traffic')

Transformation Pipeline and Model Succesfully Saved


(Pipeline(memory=None,
          steps=[('dtypes',
                  DataTypes_Auto_infer(categorical_features=[],
                                       display_types=True, features_todrop=[],
                                       id_columns=[], ml_usecase='regression',
                                       numerical_features=[],
                                       target='UNSUPERVISED_DUMMY_TARGET',
                                       time_features=[])),
                 ('imputer',
                  Simple_Imputer(categorical_strategy='most frequent',
                                 fill_value_categorical=None,
                                 fill_value_numerical=None...
                 ('fix_perfect', 'passthrough'),
                 ('clean_names', Clean_Colum_Names()),
                 ('feature_select', 'passthrough'), ('fix_multi', 'passthrough'),
                 ('dfs', 'passthrough'), ('pca', 'passthrough'),
                 ['trained_model',
                  IFo

In [21]:
traffic=load_model('traffic')

Transformation Pipeline and Model Successfully Loaded


In [22]:
traffic


Pipeline(memory=None,
         steps=[('dtypes',
                 DataTypes_Auto_infer(categorical_features=[],
                                      display_types=True, features_todrop=[],
                                      id_columns=[], ml_usecase='regression',
                                      numerical_features=[],
                                      target='UNSUPERVISED_DUMMY_TARGET',
                                      time_features=[])),
                ('imputer',
                 Simple_Imputer(categorical_strategy='most frequent',
                                fill_value_categorical=None,
                                fill_value_numerical=None...
                ('fix_perfect', 'passthrough'),
                ('clean_names', Clean_Colum_Names()),
                ('feature_select', 'passthrough'), ('fix_multi', 'passthrough'),
                ('dfs', 'passthrough'), ('pca', 'passthrough'),
                ['trained_model',
                 IForest(behaviour='ne